In [4]:
# Define constants
workbook_name = 'Publishing sites test.xlsx'
worksheet_names = ['Examples - UoE informatics', 'Examples - UoE', 'Examples - global']
site_urls_names = ['site-urls-uoe-inf.json', 'site-urls-uoe.json', 'site-urls.json']
site_scores_names = ['site-scores-uoe-inf.json', 'site-scores-uoe.json', 'site-scores.json']

lighthouse_sites_script = 'lighthouse_sites.js'
# The below line can be replaced with path to any Chromium-based browser to run Lighthouse with
chromium_path = 'C:/Program Files (x86)/Microsoft/Edge/Application/msedge.exe'

In [5]:
# Preview the data
import pandas as pd
pd.read_excel(workbook_name, sheet_name=worksheet_names[0]).head()

Name  \
0  Machine Learning and Pattern Recognition   
1           Algorithms and Data\nStructures   
2     Blockchains and \nDistributed Ledgers   
3         Computational \nCognitive Science   
4         Informatics 1 \nCognitive Science   

                                                Link       Whose resources  \
0  MLPR - Machine Learning and Pattern Recognitio...  Edinburgh University   
1     https://www.inf.ed.ac.uk/teaching/courses/ads/  Edinburgh University   
2        https://github.com/solegga/blockchaincourse  Edinburgh University   
3          https://groups.inf.ed.ac.uk/teaching/ccs/  Edinburgh University   
4  https://groups.inf.ed.ac.uk/teaching/cogsci/co...  Edinburgh University   

     Target audience                Functionality Looks (quick impression)  \
0  Students , Public               Course website                     Okay   
1   Students, Public             Course \nWebsite                     Okay   
2   Students, Public  Github Repo\nfor the course                      Meh   
3   Students, Public             Course \nWebsite                   Great!   
4   Students, Public             Course \nWebsite                   Great!   

   Site is created using Framework Double-Checked?  \
0  Plain HTML + JS + CSS                       Yes   
1  Plain HTML + JS + CSS                       Yes   
2      GitHub Repository                       Yes   
3  Hugo (Wowchemy 4.8.0)                       Yes   
4  Hugo (Wowchemy 4.8.0)                       Yes   

                      Lighthouse automatic benchmark  Lighthouse  
0  Accessibility: 100/100 (desktop), 100/100 (mob...         NaN  
1  Accessibility: 81/100 (desktop), 81/100 (mobil...         NaN  
2  Accessibility: 96/100 (desktop), 95/100 (mobil...         NaN  
3  Accessibility: 90/100 (desktop), 91/100 (mobil...         NaN  
4  Accessibility: 88/100 (desktop), 89/100 (mobil...         NaN

In [6]:
# Write JSON mapping between site names and URLs
import json
from openpyxl import load_workbook

def get_cell_hyperlink(cell):
    if cell.hyperlink is None:
        return None

    link = cell.hyperlink.target
    if cell.hyperlink.location is not None:
        link += "#" + cell.hyperlink.location
    return link

workbook = load_workbook(filename=workbook_name)
for i in range(len(worksheet_names)):
    worksheet = workbook[worksheet_names[i]]
    # Create mapping between header names (first row cells) and column indices
    headers = {c.value: c.column-1 for c in next(worksheet.iter_rows(min_row=1, max_row=1))}

    sites_urls = {}
    # Go through each data row and extract name and link
    for row in worksheet.iter_rows(min_row=2):
        if row[headers['Link']].hyperlink is not None:
            name = row[headers['Name']].value
            sites_urls[name] = get_cell_hyperlink(row[headers['Link']])

    with open(site_urls_names[i], "w", encoding="utf-8") as outfile:
        json.dump(sites_urls, outfile)

In [7]:
# Run lighthouse accessibility / performance / SEO / best practices tests
import subprocess
for i in range(len(site_urls_names)):
    with subprocess.Popen(["node", lighthouse_sites_script, chromium_path, site_urls_names[i], site_scores_names[i]],
                          stdout=subprocess.PIPE, stderr=subprocess.STDOUT) as process:
        for line in process.stdout:
            print(line.decode('utf-8'))

Producing reports for Machine Learning and Pattern Recognition

(node:12924) ExperimentalWarning: The Fetch API is an experimental feature. This feature could change at any time

(Use `node --trace-warnings ...` to show where the warning was created)

Mon, 20 Mar 2023 11:04:01 GMT LH:status Connecting to browser

Mon, 20 Mar 2023 11:04:01 GMT LH:status Navigating to about:blank

Mon, 20 Mar 2023 11:04:01 GMT LH:status Benchmarking machine

Mon, 20 Mar 2023 11:04:02 GMT LH:status Preparing target for navigation mode

Mon, 20 Mar 2023 11:04:02 GMT LH:status Navigating to about:blank

Mon, 20 Mar 2023 11:04:02 GMT LH:status Preparing target for navigation

Mon, 20 Mar 2023 11:04:02 GMT LH:status Preparing network conditions

Mon, 20 Mar 2023 11:04:02 GMT LH:status Navigating to https://mlpr.inf.ed.ac.uk/2022/

Mon, 20 Mar 2023 11:04:08 GMT LH:artifacts:getArtifact DevtoolsLog

Mon, 20 Mar 2023 11:04:08 GMT LH:artifacts:getArtifact Trace

Mon, 20 Mar 2023 11:04:08 GMT LH:artifacts:getArtif

In [8]:
# Read the produced scores and write them back to the Excel workbook
workbook = load_workbook(filename=workbook_name)

for i in range(len(worksheet_names)):
    worksheet = workbook[worksheet_names[i]]
    # Create mapping between header names (first row cells) and column indices
    headers = {c.value: c.column-1 for c in next(worksheet.iter_rows(min_row=1, max_row=1))}

    if 'Lighthouse' not in headers:
        print("Please add Lighthouse column to Excel file first, then rerun this cell!")
        # The column could be added programmatically, but too much effort to recreate headers with updated indices
    else:
        with open(site_scores_names[i], 'r', encoding="utf-8") as infile:
            scores = json.load(infile)

        for row in worksheet.iter_rows(min_row=2):
            name = row[headers['Name']].value
            if name is None:
                continue
            if name not in scores:
                print(f"No score found for {name}")
                continue
        
            lh = row[headers['Lighthouse']]
            lh.value = '\n'.join([
                f"Accessibility: {scores[name]['d_accessibility_score']}/100 (desktop), {scores[name]['m_accessibility_score']}/100 (mobile)",
                f"Performance: {scores[name]['d_performance_score']}/100 (desktop), {scores[name]['m_performance_score']}/100 (mobile)",
                f"SEO: {scores[name]['d_seo_score']}/100 (desktop), {scores[name]['m_seo_score']}/100 (mobile)",
                f"Best Practices: {scores[name]['d_best_practices_score']}/100 (desktop), {scores[name]['m_best_practices_score']}/100 (mobile)",
            ])

            min_score = min(scores[name].values())
            if min_score > 70:
                lh.style = 'Good'
            elif min_score > 50:
                lh.style = 'Neutral'
            else:
                lh.style = 'Bad'
        workbook.save(workbook_name)

No score found for Machine Learning
No score found for Applied Machine 
Learning
No score found for Introduction to Practical Programming with Objects
(Distance Learning)
